In [4]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import cm
from matplotlib.animation import FFMpegWriter
%matplotlib osx

In [12]:
# Regular SEIRD Model without variation

#Set up the ODE calculator
def VirusODE(y):
    dSdt = -y[6]*y[0]*y[2]/y[5]
    dEdt = y[6]*y[0]*y[2]/y[5] - y[7]*y[1]
    dIdt = y[7]*y[1] - y[8]*y[2] - y[9]*y[2]
    dRdt = y[8]*y[2]
    dDdt = y[9]*y[2]
    return np.array([dSdt,dEdt,dIdt,dRdt,dDdt,0,0,0,0,0,0])


def Infection(S,E,I,R,D,beta,sigma,gamma,mu,T,dt=1):
    # S is number of susceptible people
    # E is number of people that has been exposed to virus
    # I is the number of infected 
    # R is the number of cured peolpe or vaccinated
    # D is the number of death
    # N is the total population
    # Greek letters represent other coeeficients related to each category: infection rate coefficient, etc. 
    # default dt=1 day
    N = S + E + I + R + D
    y=np.array([S,E,I,R,D,N,beta,sigma,gamma,mu,0])

    St=[]
    Et=[]
    It=[]
    Rt=[]
    Dt=[]
    Nt=[]
    fig = plt.figure(figsize=(12.,6.))
    metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
    writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
    with writer.saving(fig, "initialvirus.mp4", dpi=200):
        for i in range(T):
            # Record the current data
            St.append(y[0])
            Et.append(y[1])
            It.append(y[2])
            Rt.append(y[3])
            Dt.append(y[4])
            Nt.append(y[5])

            Itotal=np.array(It)+np.array(Rt)+np.array(Dt)

            # Solve ODE with Runge-Kutta method
            dydt1=VirusODE(y)
            dydt2=VirusODE(y+0.5*dydt1*dt)
            dydt3=VirusODE(y+0.5*dydt2*dt)
            dydt4=VirusODE(y+dydt3*dt)
            y=y+dt*(dydt1+2*dydt2+2*dydt3+dydt4)/6

            #y=y+dt*VirusODE(y) Euler's Method


            # Plot the graph
            plt.clf()
            ax1 = fig.add_subplot(121)
            ax2=fig.add_subplot(122)

            ax1.plot(np.arange(i+1),St,label="Sus: "+str(round(St[-1]))+"  "+str(round(100*St[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Et,label="Exp: "+str(round(Et[-1]))+"  "+str(round(100*Et[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),It,label="Inf: "+str(round(It[-1]))+"  "+str(round(100*It[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Rt,label="Immun: "+str(round(Rt[-1]))+"  "+str(round(100*Rt[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Dt,label="Dead: "+str(round(Dt[-1]))+"  "+str(round(100*Dt[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Nt,label="Pop: "+str(round(Nt[-1])))
            ax2.plot(np.arange(i+1),Itotal,label="Cumulative number of infection: "+str(round(Itotal[-1]))+"  "+str(round(100*Itotal[-1]/N,2))+'%')
            ax1.legend()
            ax2.legend()

            #End of virus
            if len(It)>50:
                if round(It[-1])==0:
                    ax1.text(i//3,round(N*0.9),"The virus is gone, let's party",fontsize=12,bbox=dict(facecolor='blue', alpha=0.5))
                if round(It[-20])==0:
                    break

            plt.draw()
            plt.show()
            plt.pause(0.01) 
            writer.grab_frame()
            



In [13]:
#Simulation
Infection(100000000,1,1,0,0,1.38,0.19,0.3,0.05,365)

In [19]:
# First type of variation 
def variation():
    a=np.random.choice(np.array([1,2,3]))
    evo_path={1:np.array([0.1*np.random.random(),0.05*np.random.random(),-0.05*np.random.random()]),2:np.array([-0.05*np.random.random(),0.1*np.random.random(),0.05*np.random.random()]),3:np.array([0.1*np.random.random(),-0.05*np.random.random(),0.05*np.random.random()])}
    return evo_path[a]
variation()

array([-0.02283679,  0.01759135,  0.03564222])

In [20]:
#Simulate first type of variation
def Infection2(S,E,I,R,D,beta,sigma,gamma,mu,var,T,dt=1):
    N = S + E + I + R + D
    y=np.array([S,E,I,R,D,N,beta,sigma,gamma,mu,var])
    St=[]
    Et=[]
    It=[]
    Rt=[]
    Dt=[]
    Nt=[]
    ratet=[]
    fig = plt.figure(figsize=(12.,6.))
    metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
    writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
    with writer.saving(fig, "var1virus.mp4", dpi=200):
        for i in range(T):
            # Record the tendency to mutate

            rate=y[2]*y[10]
            ratet.append(rate)

            #Introduce the mutation

            if np.random.random()<rate:
                change=variation()
                if y[7]+change[0]>0 and y[9]+change[1]>0 and y[10]+change[2]>0:
                    y[7]+=change[0]
                    y[9]+=change[1] 
                    y[10]+=change[2]

            St.append(y[0])
            Et.append(y[1])
            It.append(y[2])
            Rt.append(y[3])
            Dt.append(y[4])
            Nt.append(N)
            Itotal=np.array(It)+np.array(Rt)+np.array(Dt)

            dydt1=VirusODE(y)
            dydt2=VirusODE(y+0.5*dydt1*dt)
            dydt3=VirusODE(y+0.5*dydt2*dt)
            dydt4=VirusODE(y+dydt3*dt)
            y=y+dt*(dydt1+2*dydt2+2*dydt3+dydt4)/6



            plt.clf()
            ax1 = fig.add_subplot(121)
            ax2=fig.add_subplot(122)

            ax1.plot(np.arange(i+1),St,label="Sus: "+str(round(St[-1]))+"  "+str(round(100*St[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Et,label="Exp: "+str(round(Et[-1]))+"  "+str(round(100*Et[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),It,label="Inf: "+str(round(It[-1]))+"  "+str(round(100*It[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Rt,label="Immun: "+str(round(Rt[-1]))+"  "+str(round(100*Rt[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Dt,label="Dead: "+str(round(Dt[-1]))+"  "+str(round(100*Dt[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Nt,label="Pop: "+str(round(Nt[-1])))
            ax2.plot(np.arange(i+1),Itotal,label="Cumulative number of infection: "+str(round(Itotal[-1]))+"  "+str(round(100*Itotal[-1]/N,2))+'%')
            ax1.legend()
            ax2.legend()


            if len(It)>50:
                    if round(It[-1])==0:
                        ax1.text(i//3,round(N*0.9),"The virus is gone, let's party",fontsize=12,bbox=dict(facecolor='blue', alpha=0.5))
                    if round(It[-20])==0:
                        break

            plt.draw()
            plt.pause(0.01)
            writer.grab_frame()
            

        

In [21]:
#Simulation
Infection2(100000000,1,1,0,0,1.38,0.19,0.3,0.005,0.0000001,365)

In [23]:
# Simulate second type of variation using concepts of variants: delta, alpha, etc. 
def Infection3(S,E,I,R,D,beta,sigma,gamma,mu,var,T,dt=1):
    N = S + E + I + R + D
    y=np.array([S,E,I,R,D,N,beta,sigma,gamma,mu,var])

    St=[]
    Et=[]
    It=[]
    Rt=[]
    Dt=[]
    Nt=[]
    t=0
    supp=0
    vart=False
    peak=False
    fig = plt.figure(figsize=(12.,6.))
    metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
    writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
    with writer.saving(fig, "var2virus.mp4", dpi=200):

        for i in range(T):

            if len(It)>1:
                if y[2]<It[-1]:
                    peak=True
            St.append(y[0])
            Et.append(y[1])
            It.append(y[2])
            Rt.append(y[3])
            Dt.append(y[4])
            Nt.append(y[5])
            Itotal=np.array(It)+np.array(Rt)+np.array(Dt)

            dydt1=VirusODE(y)
            dydt2=VirusODE(y+0.5*dydt1*dt)
            dydt3=VirusODE(y+0.5*dydt2*dt)
            dydt4=VirusODE(y+dydt3*dt)
            y=y+dt*(dydt1+2*dydt2+2*dydt3+dydt4)/6

            if vart:
                Itotal[start+81:]+=supp

            #Determine whether the variant occurs
            #When there is a variant, vaccine and old antibody cannot protect you anymore(immune)
            if vart!=True and np.random.random()<y[10] and peak==True:
                y[6]+=1
                y[9]+=0.005
                y[0]+=y[3]*0.7
                supp=y[3]*0.7
                y[3]*=0.3
                vart=True
                start=i-80
                pop=y[2]


            plt.clf()

            ax1 = fig.add_subplot(121)
            ax2=fig.add_subplot(122)
            ax1.plot(np.arange(i+1),St,label="Sus: "+str(round(St[-1]))+"  "+str(round(100*St[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Et,label="Exp: "+str(round(Et[-1]))+"  "+str(round(100*Et[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),It,label="Inf: "+str(round(It[-1]))+"  "+str(round(100*It[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Rt,label="Immun: "+str(round(Rt[-1]))+"  "+str(round(100*Rt[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Dt,label="Dead: "+str(round(Dt[-1]))+"  "+str(round(100*Dt[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Nt,label="Pop: "+str(round(Nt[-1])))
            ax2.plot(np.arange(i+1),Itotal,label="Cumulative number of infection: "+str(round(Itotal[-1]))+"  "+str(round(100*Itotal[-1]/N,2))+'%')


            if vart:
                ax1.text(start,pop,"Warning: Variant \u03B1 detected",fontsize=12,bbox=dict(facecolor='red', alpha=0.5))
            ax1.legend()
            ax2.legend()


            if len(It)>50:
                if round(It[-1])==0:
                    ax1.text(i//3,round(N*0.9),"The virus is gone, let's party",fontsize=12,bbox=dict(facecolor='blue', alpha=0.5))
                    if round(It[-20])==0:
                        break
            plt.draw()
            plt.pause(0.01) 
            writer.grab_frame()
            

In [24]:
#Simulation
Infection3(100000000,1,1,0,0,0.9,0.19,0.3,0.008,0.05,365)

In [25]:
# Government Response
def Infection4(S,E,I,R,D,beta,sigma,gamma,mu,var,T,dt=1):
    N = S + E + I + R + D
    y=np.array([S,E,I,R,D,N,beta,sigma,gamma,mu,var])

    St=[]
    Et=[]
    It=[]
    Rt=[]
    Dt=[]
    Nt=[]
    t=0
    supp=0
    vart=False
    peak=False
    lock_down=False
    fig = plt.figure(figsize=(12.,6.))
    metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
    writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
    with writer.saving(fig, "govvirus.mp4", dpi=200):

        for i in range(T):

            if len(It)>1:
                if y[2]<It[-1]:
                    peak=True
            St.append(y[0])
            Et.append(y[1])
            It.append(y[2])
            Rt.append(y[3])
            Dt.append(y[4])
            Nt.append(y[5])
            Itotal=np.array(It)+np.array(Rt)+np.array(Dt)

            dydt1=VirusODE(y)
            dydt2=VirusODE(y+0.5*dydt1*dt)
            dydt3=VirusODE(y+0.5*dydt2*dt)
            dydt4=VirusODE(y+dydt3*dt)
            y=y+dt*(dydt1+2*dydt2+2*dydt3+dydt4)/6

            if vart:
                Itotal[start+81:]+=supp

            #Government response
            if Itotal[-1]>100000:
                lock_down=True
                y[6]*=0.1



            #Determine whether the variant occurs
            if vart!=True and np.random.random()<y[10] and peak==True:
                y[6]+=1
                y[9]+=0.005
                y[0]+=y[3]*0.7
                supp=y[3]*0.7
                y[3]*=0.3
                vart=True
                start=i-80
                pop=y[2]


            plt.clf()

            ax1 = fig.add_subplot(121)
            ax2=fig.add_subplot(122)
            ax1.plot(np.arange(i+1),St,label="Sus: "+str(round(St[-1]))+"  "+str(round(100*St[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Et,label="Exp: "+str(round(Et[-1]))+"  "+str(round(100*Et[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),It,label="Inf: "+str(round(It[-1]))+"  "+str(round(100*It[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Rt,label="Immun: "+str(round(Rt[-1]))+"  "+str(round(100*Rt[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Dt,label="Dead: "+str(round(Dt[-1]))+"  "+str(round(100*Dt[-1]/N,2))+'%')
            ax1.plot(np.arange(i+1),Nt,label="Pop: "+str(round(Nt[-1])))
            ax2.plot(np.arange(i+1),Itotal,label="Cumulative number of infection: "+str(round(Itotal[-1]))+"  "+str(round(100*Itotal[-1]/N,2))+'%')
            if lock_down:
                ax2.text(15,100000,"Warning: Lock-down begins",fontsize=12,bbox=dict(facecolor='yellow', alpha=0.5))



            if vart:
                ax1.text(start,pop,"Warning: Variant \u03B1 detected",fontsize=12,bbox=dict(facecolor='red', alpha=0.5))
            ax1.legend()
            ax2.legend()


            if len(It)>50:
                if round(It[-1])==0:
                    ax1.text(i//3,round(N*0.9),"The virus is gone, let's party",fontsize=12,bbox=dict(facecolor='blue', alpha=0.5))
                    if round(It[-20])==0:
                        break
            plt.draw()
            plt.pause(0.01) 
            writer.grab_frame()


In [26]:
Infection4(100000000,1,1,0,0,0.9,0.19,0.3,0.008,0.05,365)